In [225]:
from bs4 import BeautifulSoup
import requests
import pandas as pd

In [226]:
#print(headers)

In [227]:
zipcode = '02145'
#zipcode = '27601'
base_url = 'http://www.realtor.com/realestateandhomes-search/' + zipcode + '?pgsz=50'

params = {'user_agent':''}
requests.utils.default_user_agent()
headers = requests.utils.default_headers()
headers['User-Agent'] = 'Mozilla/5.2'
response = requests.get(base_url+zipcode, headers=headers)

In [228]:
data = response.text
soup = BeautifulSoup(data, 'html.parser')


In [229]:
soup

<!DOCTYPE html>

<html lang="en">
<head>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="app-id=com.move.realtor" name="google-play-app">
<meta content="width=device-width, initial-scale=1, maximum-scale=1, user-scalable=no" name="viewport">
<meta content="#d92228" name="theme-color">
<meta content="02145 real estate listings are available on realtor.com&amp;reg; right now. Check out 02145 homes for sale and other real estate listings for Somerville, MA 02145." name="description"/>
<meta content="authenticity_token" name="csrf-param"/>
<meta content="IVrBs6a6+PpAry0y0IchWvy8W0FInduwpDXoK8MMtiJjbBV2kY38slvNEWakUEkGLmIJ0ZyPHvHLqIaMdbLxAA==" name="csrf-token"/>
<meta content="" property="og:url"/>
<meta content="" property="og:title"/>
<meta content="" property="og:description"/>
<meta content="https://ap.rdcpix.com/890785894/db9f1474607e5578964e238e9f94a809l-m0xd-w480_h480_q80.jpg" property="og:image"/>
<meta content="realtor.com®" property="og:site_name"/>
<meta co

In [230]:
house_data_list_of_lists = []
for i in soup.find_all('div',{'class':'srp-item-details'}):
    this_house = []
    house_price = i.find('div',{'class':'srp-item-price'}).next_element
    
    bedrooms = i.find('li',{'data-label':'property-meta-beds'})
    bedrooms = BeautifulSoup(str(bedrooms),'html.parser')
    bedrooms = bedrooms.find('span',{'class','data-value'})
    bedrooms = BeautifulSoup(str(bedrooms),'html.parser')
    bedrooms = bedrooms.text
    
    bathrooms = i.find('li',{'data-label':'property-meta-baths'})
    bathrooms = BeautifulSoup(str(bathrooms),'html.parser')
    bathrooms = bathrooms.find('span',{'class','data-value'})
    bathrooms = BeautifulSoup(str(bathrooms),'html.parser')
    bathrooms = bathrooms.text
    
    squar_footage = i.find('li',{'data-label':'property-meta-sqft'})
    squar_footage = BeautifulSoup(str(squar_footage),'html.parser')
    squar_footage = squar_footage.find('span',{'class','data-value'})
    squar_footage = BeautifulSoup(str(squar_footage),'html.parser')
    squar_footage = squar_footage.text
    
    zip_code = i.find('span',{'class','listing-postal'}).next_element
    
    neighborhood = i.find('div',{'class','srp-item-neighborhood ellipsis link-tertiary hidden-xxs hidden-xs'})
    neighborhood = BeautifulSoup(str(neighborhood),'html.parser')
    neighborhood = neighborhood.text
    
    this_house.append(house_price)
    this_house.append(bedrooms)
    this_house.append(bathrooms)
    this_house.append(squar_footage)
    house_data_list_of_lists.append(this_house)
    this_house.append(zip_code)
    this_house.append(neighborhood)
    
    
house_data_list_of_lists

[['\n          $1,250,000\n        ',
  '3',
  '3+',
  '2,305',
  '02145',
  '\nMagoun Square\n'],
 ['\n          $2,200,000\n        ',
  '4',
  '10+',
  '8,959',
  '02145',
  '\nEast Somerville\n'],
 ['\n          $2,200,000\n        ',
  'None',
  'None',
  'None',
  '02145',
  '\nEast Somerville\n'],
 ['\n          $1,596,000\n        ', '2', '2+', '1,593', '02145', 'None'],
 ['\n          $619,000\n        ',
  '3',
  '1+',
  '1,723',
  '02145',
  '\nWinter Hill\n'],
 ['\n          $519,000\n        ',
  '3',
  '1',
  '1,392',
  '02145',
  '\nTen Hills\n'],
 ['\n          $699,000\n        ',
  '3',
  '2+',
  '1,716',
  '02145',
  '\nWinter Hill\n'],
 ['\n          $749,000\n        ',
  '4',
  '1',
  '1,942',
  '02145',
  '\nWinter Hill\n'],
 ['\n          $699,900\n        ',
  '2',
  '2',
  '1,860',
  '02145',
  '\nEast Somerville\n'],
 ['\n          $549,900\n        ',
  '2',
  '1',
  '1,211',
  '02145',
  '\nTen Hills\n'],
 ['\n          $826,500\n        ', '2', '2', '1,092

In [231]:
housing_df = pd.DataFrame(house_data_list_of_lists, columns = ['price','bedroom','bathroom','sqft','zip','neighborhood'])
housing_df['price'] = housing_df['price'].astype('str')

In [235]:
import re
def clean_price_column(series):
    series = re.sub('[\n$, ]','',series)
    return(series)

def clean_neighborhood_column(series):
    series = re.sub('[\n ]','',series)
    return(series)

def clean_sqft_columns(series):
    series = re.sub('[,]','',series)
    return(series)

In [233]:
housing_df['price'] = housing_df['price'].apply(clean_price_column).astype(int)
housing_df['neighborhood'] = housing_df['neighborhood'].apply(clean_neighborhood_column)

In [236]:
housing_df['sqft'] = housing_df['sqft'].apply(clean_sqft_columns)

In [237]:
housing_df

price bedroom bathroom  sqft    zip    neighborhood
0   1250000       3       3+  2305  02145    MagounSquare
1   2200000       4      10+  8959  02145  EastSomerville
2   2200000    None     None  None  02145  EastSomerville
3   1596000       2       2+  1593  02145            None
4    619000       3       1+  1723  02145      WinterHill
5    519000       3        1  1392  02145        TenHills
6    699000       3       2+  1716  02145      WinterHill
7    749000       4        1  1942  02145      WinterHill
8    699900       2        2  1860  02145  EastSomerville
9    549900       2        1  1211  02145        TenHills
10   826500       2        2  1092  02145            None
11   579000       2        2  1111  02145  EastSomerville
12   849999       6        2  2281  02145        TenHills
13   752500       1        1   820  02145            None
14  1100000       9        3  3922  02145        TenHills
15   724900       2        2  1826  02145  EastSomerville
16   689900       2        2  1545  02145        TenHills
17   705000       2        3  1656  02145      WinterHill
18   695000       4       3+  1379  02145      WinterHill
19   769000       3        2  1400  02145      WinterHill
20   619900       3        2  1120  02145  EastSomerville
21  1227900       2        2  1178  02145            None
22   499000       2        2   850  02145  EastSomerville
23   548900       0        1   506  02145            None
24   639900       1        1   761  02145            None
25   729900       5        3  2051  02145        TenHills
26   875000       3       3+  2045  02145        TenHills

In [188]:
import pandas as pd
import zipfile

zf = zipfile.ZipFile('./Datasets/Zip.zip') # having First.csv zipped file.

In [189]:
median_rent_1_bd = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_1Bedroom.csv')) 
median_rent_2_bd = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_2Bedroom.csv'))
median_rent_3_bd = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_3Bedroom.csv'))
median_rent_4_bd = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_4Bedroom.csv'))
median_rent_5_bd = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_5BedroomOrMore.csv'))
median_rent_all = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_AllHomes.csv'))
median_rent_studio = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_Studio.csv'))
median_rent_SFH = pd.read_csv(zf.open('Zip/Zip_MedianRentalPrice_Sfr.csv'))

In [108]:
median_rent_2_bd.columns

Index(['RegionName', 'City', 'State', 'Metro', 'CountyName', 'SizeRank',
       '2010-02', '2010-03', '2010-04', '2010-05', '2010-06', '2010-07',
       '2010-08', '2010-09', '2010-10', '2010-11', '2010-12', '2011-01',
       '2011-02', '2011-03', '2011-04', '2011-05', '2011-06', '2011-07',
       '2011-08', '2011-09', '2011-10', '2011-11', '2011-12', '2012-01',
       '2012-02', '2012-03', '2012-04', '2012-05', '2012-06', '2012-07',
       '2012-08', '2012-09', '2012-10', '2012-11', '2012-12', '2013-01',
       '2013-02', '2013-03', '2013-04', '2013-05', '2013-06', '2013-07',
       '2013-08', '2013-09', '2013-10', '2013-11', '2013-12', '2014-01',
       '2014-02', '2014-03', '2014-04', '2014-05', '2014-06', '2014-07',
       '2014-08', '2014-09', '2014-10', '2014-11', '2014-12', '2015-01',
       '2015-02', '2015-03', '2015-04', '2015-05', '2015-06', '2015-07',
       '2015-08', '2015-09', '2015-10', '2015-11', '2015-12', '2016-01',
       '2016-02', '2016-03', '2016-04', '2016-05', 

In [109]:
def fix_zipcode_leading_zeroes(zip_column):
    zip_column = str(zip_column)
    if len(zip_column) < 5:
        zip_column =  '0' + zip_column
    return(zip_column)

In [110]:
#fix zipcodes for all rent dataframes#

for i in [median_rent_1_bd,median_rent_2_bd,median_rent_3_bd,median_rent_4_bd,median_rent_5_bd,median_rent_all,median_rent_SFH,median_rent_studio]:
    i['RegionName'] = i['RegionName'].apply(fix_zipcode_leading_zeroes)


In [112]:
for i in [median_rent_1_bd,median_rent_2_bd,median_rent_3_bd,median_rent_4_bd,median_rent_5_bd,median_rent_all,median_rent_SFH,median_rent_studio]:
    for j in i:
        print(i.iloc[:,-12:])
        #i['mean rent 2016'] = i.iloc[:,-12:].mean()

     2016-01  2016-02  2016-03  2016-04  2016-05  2016-06  2016-07  2016-08  \
0     3050.0   3050.0   3069.0   3000.0   3100.0   3040.0   3000.0   3000.0   
1     1325.0   1347.5   1395.0   1397.5   1395.0   1400.0   1395.0   1380.0   
2     3300.0   3300.0   3350.0   3300.0   3300.0   3300.0   3109.0   3300.0   
3     1525.0   1650.0   1550.0   1545.0   1475.0   1495.0   1465.0   1550.0   
4     2695.0   2682.5   2675.0   2690.0   2595.0   2625.0   2600.0   2650.0   
5     1175.0   1195.0   1175.0   1175.0   1182.5   1197.5   1195.0   1175.0   
6     1350.0   1350.0   1350.0   1350.0   1332.5   1350.0   1350.0   1350.0   
7     3200.0   3397.5   3395.0   3197.5   3322.5   3200.0   3100.0   2895.0   
8      946.0    990.0    970.0    979.0   1024.0    990.5   1051.0   1056.0   
9     1600.0   1600.0   1625.0   1600.0   1600.0   1600.0   1750.0   1695.0   
10    1029.0   1039.0   1205.0   1057.0   1095.5   1104.0   1127.0   1225.0   
11    1875.0   1885.0   1850.0   1900.0   1950.0   1

In [76]:
cambr_1_bd = median_rent_1_bd[median_rent_1_bd['City']=='Cambridge']
cambr_1_bd['num_bedrooms'] = 1
cambr_2_bd = median_rent_2_bd[median_rent_2_bd['City']=='Cambridge']
cambr_2_bd['num_bedrooms'] = 2
cambr_3_bd = median_rent_3_bd[median_rent_3_bd['City']=='Cambridge']
cambr_3_bd['num_bedrooms'] = 3
cambr_4_bd = median_rent_4_bd[median_rent_4_bd['City']=='Cambridge']
cambr_4_bd['num_bedrooms'] = 4
cambr_5_bd = median_rent_5_bd[median_rent_5_bd['City']=='Cambridge']
cambr_5_bd['num_bedrooms'] = 5
cambr_all_bd = median_rent_all[median_rent_all['City']=='Cambrdige']
cambr_all_bd['num_bedrooms'] = 'all'


C:\Users\USER\Anaconda3\lib\site-packages\ipykernel\__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
C:\Users\USER\Anaconda3\lib\site-packages\ipykernel\__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
C:\Users\USER\Anaconda3\lib\site-packages\ipykernel\__main__.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pand

In [77]:
cambr_2_bd

RegionName       City State   Metro CountyName  SizeRank  2010-02  \
414        2139  Cambridge    MA  Boston  Middlesex       415      NaN   
417        2138  Cambridge    MA  Boston  Middlesex       418      NaN   
602        2140  Cambridge    MA  Boston  Middlesex       603      NaN   
631        2141  Cambridge    MA  Boston  Middlesex       632      NaN   
649        2142  Cambridge    MA  Boston  Middlesex       650      NaN   

     2010-03  2010-04  2010-05      ...       2016-04  2016-05  2016-06  \
414      NaN      NaN      NaN      ...        2800.0   2900.0   2797.5   
417      NaN      NaN      NaN      ...        2700.0   2800.0   2800.0   
602      NaN      NaN      NaN      ...        2800.0   2857.0   2750.0   
631      NaN      NaN      NaN      ...        2500.0   2575.0   2525.0   
649      NaN      NaN      NaN      ...        3538.0   3641.5   3539.0   

     2016-07  2016-08  2016-09  2016-10  2016-11  2016-12  num_bedrooms  
414   2765.0   2800.0   2750.0   2850.0   2800.0   2800.0             2  
417   2797.5   2700.0   2758.0   2650.0   2587.5   2600.0             2  
602   2648.0   2679.0   2679.0   2650.0   2650.0   2650.0             2  
631   2600.0   2550.0   2575.0   3000.0   2837.5   2750.0             2  
649   3139.5   3468.0   3367.0   3501.0   3366.0   3500.0             2  

[5 rows x 90 columns]

In [78]:
cambr_2_bd_2016_med_rent = cambr_2_bd.drop(cambr_2_bd.columns[6:-13],axis=1)

In [79]:
cambr_2_bd_2016_med_rent['2016 average median rent'] = cambr_2_bd_2016_med_rent.iloc[:,6:18].mean(axis=1)

In [80]:
cambr_2_bd_2016_med_rent

RegionName       City State   Metro CountyName  SizeRank  2016-01  \
414        2139  Cambridge    MA  Boston  Middlesex       415   2700.0   
417        2138  Cambridge    MA  Boston  Middlesex       418   2600.0   
602        2140  Cambridge    MA  Boston  Middlesex       603   2722.0   
631        2141  Cambridge    MA  Boston  Middlesex       632   2450.0   
649        2142  Cambridge    MA  Boston  Middlesex       650   3600.0   

     2016-02  2016-03  2016-04  2016-05  2016-06  2016-07  2016-08  2016-09  \
414   2700.0   2700.0   2800.0   2900.0   2797.5   2765.0   2800.0   2750.0   
417   2700.0   2700.0   2700.0   2800.0   2800.0   2797.5   2700.0   2758.0   
602   2758.0   2800.0   2800.0   2857.0   2750.0   2648.0   2679.0   2679.0   
631   2500.0   2575.0   2500.0   2575.0   2525.0   2600.0   2550.0   2575.0   
649   3519.5   3582.0   3538.0   3641.5   3539.0   3139.5   3468.0   3367.0   

     2016-10  2016-11  2016-12  num_bedrooms  2016 average median rent  
414   2850.0   2800.0   2800.0             2               2780.208333  
417   2650.0   2587.5   2600.0             2               2699.416667  
602   2650.0   2650.0   2650.0             2               2720.250000  
631   3000.0   2837.5   2750.0             2               2619.791667  
649   3501.0   3366.0   3500.0             2               3480.125000

In [ ]:
t